In [1]:
from pathlib import Path
from src.notebookcodesnippets.hideInputs import hide_toggle 

hide_toggle()

In [2]:
from IPython.display import display, Markdown

with open(Path.cwd().parent.parent.parent / "src" / "notebookcodesnippets" / "supervised" / "intro.md", 'r') as fh:
    content = fh.read()

display(Markdown(content))
hide_toggle()

# 05-Supervised learning

In this notebook we will train a model based on the previous 4 notebooks. This includes inspecting, finding the optimal hyperparameters (with many visualizations) and finally predict with the optimal model that has been found. This notebook is the same as every other supervised notebook in this project, but differs in training set, principal components and results. Therefore, to provide easy implementations, the notebook has been made modular to a certain degree, in particular for further implementation of other machine learning algorithms. It should be relatively straight forward to add more algorithms.

## Table of contents

- Imports and reading of data
- Algorithms
- Methods for finding optimal hyperparameters
- Optimal hyperparameter search
    - Visualizing the optimal parameters for dimensionality reduction
    - Visualizing confusion metrics
    - ROC-AUC  and precision recall curves
    - Visualizing the cross-validated trained models
    - Visualizing relevant features
    - Falsely predicted entries
- Predicting solid-state qubit candidates
    - Save the summary and models

The cell under provides the editorial difference between the different supervised notebooks in this project. 


In [3]:
title = "Ferrenti"
InsertApproach = "01-ferrenti-approach"
numberOfPrincipalComponents = 176

# Imports and reading of data

Most of the code used in this notebook is found in the src library.

In [4]:
# Optional: Load the "autoreload" extension so that code can change
%load_ext autoreload

#OPTIONAL: Always reload modules so that as you change code in src, it gets loaded
%autoreload 2

hide_toggle()

In [5]:
import sys
sys.path.insert(0, "../")

data_dir = Path.cwd().parent.parent.parent / "data"
print("Current data directory {}".format(data_dir))
models_dir = Path.cwd().parent.parent.parent / "models" 

# src
from src.models import train_model, predict_model
from src.features import build_features
from src.visualization import visualize

#Standard libraries
import numpy as np
import pandas as pd
import pickle

#Models
from sklearn.ensemble import RandomForestClassifier, GradientBoostingClassifier
from sklearn.linear_model import LogisticRegression
from sklearn.tree import DecisionTreeClassifier

# CV
from sklearn.model_selection import RepeatedStratifiedKFold

#visualizations
import plotly.graph_objs as go
from tqdm import tqdm

# setting random seed for reproducibility
random_state=1
hide_toggle()

Current data directory /Users/oliverhebnes/Documents/predicting-solid-state-qubit-material-hosts/data

If you use the ChemEnv tool for your research, please consider citing the following reference(s) :
David Waroquiers, Xavier Gonze, Gian-Marco Rignanese, Cathrin Welker-Nieuwoudt, Frank Rosowski,
Michael Goebel, Stephan Schenk, Peter Degelmann, Rute Andre, Robert Glaum, and Geoffroy Hautier,
"Statistical analysis of coordination environments in oxides",
Chem. Mater., 2017, 29 (19), pp 8346-8360,
DOI: 10.1021/acs.chemmater.7b02766



In [6]:
data   = pd.read_pickle(data_dir / "processed" / "processedData.pkl")
trainingData   = pd.read_pickle(data_dir / InsertApproach / "processed" / "trainingData.pkl")
trainingTarget= pd.read_pickle(data_dir / InsertApproach / "processed" / "trainingTarget.pkl")
testSet       = pd.read_pickle(data_dir / InsertApproach / "processed" / "testSet.pkl")

trainingData

material_id  full_formula  AtomicOrbitals|HOMO_character  \
0           mp-7            S6                            2.0   
1          mp-14           Se3                            2.0   
2          mp-19           Te3                            2.0   
3          mp-47            C4                            2.0   
4          mp-66            C2                            2.0   
...          ...           ...                            ...   
1520  mp-1275839  Co4Bi24S8O64                            3.0   
1521  mp-1291058  Sr4Mn2Mo2O12                            3.0   
1522  mp-1291630       Fe12O16                            3.0   
1523  mp-1298346     Sr8Co4O16                            3.0   
1524  mp-1539137      Rb1Cr5S8                            3.0   

      AtomicOrbitals|HOMO_element  AtomicOrbitals|HOMO_energy  \
0                              16                   -0.261676   
1                              34                   -0.245806   
2                              52                   -0.226594   
3                               6                   -0.199186   
4                               6                   -0.199186   
...                           ...                         ...   
1520                           27                   -0.322368   
1521                           25                   -0.266540   
1522                           26                   -0.295049   
1523                           27                   -0.322368   
1524                           24                   -0.118123   

      AtomicOrbitals|LUMO_character  AtomicOrbitals|LUMO_element  \
0                               2.0                           16   
1                               2.0                           34   
2                               2.0                           52   
3                               2.0                            6   
4                               2.0                            6   
...                             ...                          ...   
1520                            3.0                           27   
1521                            3.0                           25   
1522                            3.0                           26   
1523                            3.0                           27   
1524                            3.0                           24   

      AtomicOrbitals|LUMO_energy  \
0                      -0.261676   
1                      -0.245806   
2                      -0.226594   
3                      -0.199186   
4                      -0.199186   
...                          ...   
1520                   -0.322368   
1521                   -0.266540   
1522                   -0.295049   
1523                   -0.322368   
1524                   -0.118123   

      AtomicPackingEfficiency|dist from 1 clusters |APE| < 0.010  \
0                                              1.000000            
1                                              1.000000            
2                                              1.000000            
3                                              1.000000            
4                                              1.000000            
...                                                 ...            
1520                                           0.034641            
1521                                           0.052116            
1522                                           0.091832            
1523                                           0.057864            
1524                                           0.033111            

      AtomicPackingEfficiency|dist from 3 clusters |APE| < 0.010  ...  \
0                                              1.000000           ...   
1                                              1.000000           ...   
2                                              1.000000           ...   
3                                              1.000000           ...   
4          

In [7]:
testSet

material_id pretty_formula   full_formula  candidate  \
1525    mvc-12905           FeO2          Fe4O8        NaN   
1526        mp-24              C             C8        NaN   
1527        mp-25             N2             N8        NaN   
1528       mp-111             Ne            Ne1        NaN   
1529       mp-118              P            P24        NaN   
...           ...            ...            ...        ...   
25196  mp-1304797      Sr3InNiO6  Sr12In4Ni4O24        NaN   
25197  mp-1541522          BiPO4        Bi2P2O8        NaN   
25198  mp-1541714      Cs3As2Cl9      Cs3As2Cl9        NaN   
25199  mp-1542038        CsSnSe3      Cs2Sn2Se6        NaN   
25200  mp-1542939     BaMo(PO4)2     Ba1Mo1P2O8        NaN   

       AtomicOrbitals|HOMO_character  AtomicOrbitals|HOMO_element  \
1525                             3.0                           26   
1526                             2.0                            6   
1527                             2.0                            7   
1528                            -1.0                           -1   
1529                             2.0                           15   
...                              ...                          ...   
25196                            2.0                            8   
25197                            2.0                            8   
25198                            2.0                           17   
25199                            2.0                           34   
25200                            2.0                            8   

       AtomicOrbitals|HOMO_energy  AtomicOrbitals|LUMO_character  \
1525                    -0.295049                            3.0   
1526                    -0.199186                            2.0   
1527                    -0.266297                            2.0   
1528                     0.000000                           -1.0   
1529                    -0.206080                            2.0   
...                           ...                            ...   
25196                   -0.338381                            2.0   
25197                   -0.338381                            2.0   
25198                   -0.320380                            2.0   
25199                   -0.245806                            2.0   
25200                   -0.338381                            2.0   

       AtomicOrbitals|LUMO_element  AtomicOrbitals|LUMO_energy  ...  \
1525                            26                   -0.295049  ...   
1526                             6                   -0.199186  ...   
1527                             7                   -0.266297  ...   
1528                            -1                    0.000000  ...   
1529                            15                   -0.206080  ...   
...                            ...                         ...  ...   
25196                            8                   -0.338381  ...   
25197                            8                   -0.338381  ...   
25198                           33                   -0.197497  ...   
25199                           34                   -0.245806  ...   
25200                            8                   -0.338381  ...   

       AFLOWML|ml_agl_heat_capacity_Cv_300K_per_atom  \
1525                                           2.488   
1526                                           0.634   
1527                                           2.612   
1528                                           2.889   
1529                                           2.713   
...                                              ...   
25196                                          2.753   
25197                                          2.710   
25198                                          2.963   
25199                                          2.938   
25200                                          2.620   

       AFLOWML|ml_agl_thermal_conductivity_300K  \
1525                                  

In [8]:
from IPython.display import display, Markdown

with open(Path.cwd().parent.parent.parent / "src" / "notebookcodesnippets" / "supervised" / "algorithms.md", 'r') as fh:
    content = fh.read()

display(Markdown(content))
hide_toggle()

# Algorithms
Below we define the algorithm to use and its abbreviation. Parameters that are optional to tune are the parameters to the algorithms, with the default value as their optimised value. Another parameter to tune is how many cross-validations one wants to iterate through for the analysis. In addition, one has to find the best features for a new algorithm which will be added further down in the notebook.


In [9]:
InsertAlgorithms    = [LogisticRegression        (random_state = random_state, max_iter=200),
                       DecisionTreeClassifier    (random_state = random_state, max_features = "auto"),
                       RandomForestClassifier    (random_state = random_state, max_features = "auto", max_depth=6),\
                       GradientBoostingClassifier(random_state = random_state, max_features = "auto")]
InsertAbbreviations = ["LOG", "DT", "RF", "GB"]
InsertprettyNames   = ["Logistic regression", "Decision Tree", "Random Forest", "Gradient Boost"]

In [10]:
from IPython.display import display, Markdown

with open(Path.cwd().parent.parent.parent / "src" / "notebookcodesnippets" / "supervised" / "optimalparameters.md", 'r') as fh:
    content = fh.read()

display(Markdown(content))
hide_toggle()

# Methods for finding optimal hyperparameters

### Cross-validation

Cross-validation is a technique to evaluate predictive models by partitioning the original sample into a training set to train the model, and a test set to evaluate it. It is crucial that we avoid at all cost to fit anything to the test data, since this will introduce bias in the model and might reduce the generalization potential of a model.

### k-fold cross-validation

In k-fold cross-validation, the sample is partioned into k equal sized subsamples. Of the k samples, a single sample is used as validation set while the remaining k-1 samples are used as training data. The process is then repeated k-times, such that each of the k-th subsample is used as validation set exactly one time. Therefore, all observations are used for both training and validation, and each observation is used for validation exactly once. The k results from the folds can then be averaged to produce an estimate.

### Stratified k-fold cross-validation

In stratified k-fold cross validation, the fold that is selected contains roughly the same proportions of existing class labels.

### n-repeated stratified k-fold cross-validation

In n-repeated stratified k-fold cross-validation, the stratified k-fold cross-validation is repeated n times, which yields n random partitions of the original sample. The n results can be averaged to produce a single estimation.

## Sample size
To not discrimate a class, we make sure that each class is equally represented in the subsamples. Underneath shows a brief overview of the different methods involved to deal with this challenge.

### Random oversampling of minority class

Random oversampling can be achived by randomly duplicating examples from the minority class and adding them to the training dataset.

The approach can be effective to algorithms that are vulnerable to a skewed dsitribution, however, it can also affect algorithms to overfit the minority class.

### Random Undersampling of majority class

Random undersampling involves randomly selecting examples from the majority class to delete from the training dataset.

This can prove problematic, since the loss of data can make the decision boundary between minority and majority instances harder to learn. Additionally, there is a chance that the model might loose valuable information.

### Both oversampling and undersampling

A third option might be to combine the two of them.


# Optimal hyperparameters search

In this section we will find the optimal parameters used for the various algorithms. We will use imblearn's Pipeline to provide the option of implementing sampling such as SMOTE and RandomUnderSampler. The advantage of using imblearn instead of sklearn, is that sklearn's pipeline will fit the samplers to the validation data as well, while imblearn only fit the resamplers to the training data. We store the best estimators and use them again under this section.

It is possible to have a large search over a wide amount of properties, but that is indeed extremely cpu-demanding. Therefore, we restrict ourself to the standard choice of some properties, but include a search for properties that can reduce the variance.

## Standardscaler and principal component analysis
Since we will scale the data, it is neccessary to combine the target and training data and scale it together. We fit the standardscaler to the training data, and then transform the test data with the same scaling as we fitted from the training data. Thereafter, we will apply a principal component analysis to potentially reduce the dimensions of the data.


In [11]:
# Optional to include any sampling method. Default is none. 
includeSampleMethods = [""]#, "under", "over", "both"]

In [12]:
numberRuns   = 5
numberSplits = 5

rskfold = RepeatedStratifiedKFold(n_splits=numberSplits, n_repeats=numberRuns, random_state=random_state)

In [ ]:
ModelsBestParams = pd.Series({}, dtype="string")

Abbreviations = []
prettyNames   = []
Algorithms = []

for i, algorithm in tqdm(enumerate(InsertAlgorithms)):
    for method in includeSampleMethods:
        print("Finding best params for: {}".format(InsertAbbreviations[i] + " " + method))
        bestEstimator, ModelsBestParams[InsertAbbreviations[i] + " " + method] = train_model.applyGridSearch(
                                                                             X = trainingData.drop(["material_id", "full_formula"], axis=1), 
                                                                             y = trainingTarget.values.reshape(-1,),
                                                                        model = algorithm, 
                                                                           cv = rskfold,
                                                                        numPC = numberOfPrincipalComponents,
                                                                 sampleMethod = method,
                                                                     searchPC = True )
        Abbreviations.append(InsertAbbreviations[i] + " " + method)
        prettyNames.append(InsertAbbreviations[i] + " " + method)
        Algorithms.append(bestEstimator)

0it [00:00, ?it/s]

Finding best params for: LOG 
Fitting 25 folds for each of 1232 candidates, totalling 30800 fits
[CV] END model__C=0.001, model__max_iter=200, model__penalty=l2, pca__n_components=1; total time=   0.2s
[CV] END model__C=0.001, model__max_iter=200, model__penalty=l2, pca__n_components=1; total time=   0.2s
[CV] END model__C=0.001, model__max_iter=200, model__penalty=l2, pca__n_components=1; total time=   0.1s
[CV] END model__C=0.001, model__max_iter=200, model__penalty=l2, pca__n_components=1; total time=   0.1s
[CV] END model__C=0.001, model__max_iter=200, model__penalty=l2, pca__n_components=1; total time=   0.2s
[CV] END model__C=0.001, model__max_iter=200, model__penalty=l2, pca__n_components=1; total time=   0.1s
[CV] END model__C=0.001, model__max_iter=200, model__penalty=l2, pca__n_components=1; total time=   0.1s
[CV] END model__C=0.001, model__max_iter=200, model__penalty=l2, pca__n_components=3; total time=   0.1s
[CV] END model__C=0.001, model__max_iter=200, model__penalty=l2

[CV] END model__C=0.001, model__max_iter=200, model__penalty=l2, pca__n_components=1; total time=   0.2s
[CV] END model__C=0.001, model__max_iter=200, model__penalty=l2, pca__n_components=1; total time=   0.1s
[CV] END model__C=0.001, model__max_iter=200, model__penalty=l2, pca__n_components=1; total time=   0.2s
[CV] END model__C=0.001, model__max_iter=200, model__penalty=l2, pca__n_components=1; total time=   0.2s
[CV] END model__C=0.001, model__max_iter=200, model__penalty=l2, pca__n_components=3; total time=   0.2s
[CV] END model__C=0.001, model__max_iter=200, model__penalty=l2, pca__n_components=3; total time=   0.1s
[CV] END model__C=0.001, model__max_iter=200, model__penalty=l2, pca__n_components=3; total time=   0.1s
[CV] END model__C=0.001, model__max_iter=200, model__penalty=l2, pca__n_components=3; total time=   0.1s
[CV] END model__C=0.001, model__max_iter=200, model__penalty=l2, pca__n_components=5; total time=   0.1s
[CV] END model__C=0.001, model__max_iter=200, model__pe

[CV] END model__C=0.001, model__max_iter=200, model__penalty=l2, pca__n_components=1; total time=   0.2s
[CV] END model__C=0.001, model__max_iter=200, model__penalty=l2, pca__n_components=1; total time=   0.1s
[CV] END model__C=0.001, model__max_iter=200, model__penalty=l2, pca__n_components=1; total time=   0.2s
[CV] END model__C=0.001, model__max_iter=200, model__penalty=l2, pca__n_components=1; total time=   0.1s
[CV] END model__C=0.001, model__max_iter=200, model__penalty=l2, pca__n_components=3; total time=   0.2s
[CV] END model__C=0.001, model__max_iter=200, model__penalty=l2, pca__n_components=3; total time=   0.1s
[CV] END model__C=0.001, model__max_iter=200, model__penalty=l2, pca__n_components=3; total time=   0.1s
[CV] END model__C=0.001, model__max_iter=200, model__penalty=l2, pca__n_components=3; total time=   0.1s
[CV] END model__C=0.001, model__max_iter=200, model__penalty=l2, pca__n_components=3; total time=   0.1s
[CV] END model__C=0.001, model__max_iter=200, model__pe

[CV] END model__C=0.001, model__max_iter=200, model__penalty=l2, pca__n_components=1; total time=   0.2s
[CV] END model__C=0.001, model__max_iter=200, model__penalty=l2, pca__n_components=3; total time=   0.2s
[CV] END model__C=0.001, model__max_iter=200, model__penalty=l2, pca__n_components=5; total time=   0.3s
[CV] END model__C=0.001, model__max_iter=200, model__penalty=l2, pca__n_components=5; total time=   0.1s
[CV] END model__C=0.001, model__max_iter=200, model__penalty=l2, pca__n_components=5; total time=   0.1s
[CV] END model__C=0.001, model__max_iter=200, model__penalty=l2, pca__n_components=7; total time=   0.1s
[CV] END model__C=0.001, model__max_iter=200, model__penalty=l2, pca__n_components=7; total time=   0.1s
[CV] END model__C=0.001, model__max_iter=200, model__penalty=l2, pca__n_components=7; total time=   0.1s
[CV] END model__C=0.001, model__max_iter=200, model__penalty=l2, pca__n_components=9; total time=   0.2s
[CV] END model__C=0.001, model__max_iter=200, model__pe

...

[CV] END model__max_depth=1, model__max_features=auto, pca__n_components=157; total time=   4.6s
[CV] END model__max_depth=1, model__max_features=auto, pca__n_components=159; total time=   4.2s
[CV] END model__max_depth=1, model__max_features=auto, pca__n_components=159; total time=17.4min
[CV] END model__max_depth=1, model__max_features=auto, pca__n_components=161; total time=   4.7s
[CV] END model__max_depth=1, model__max_features=auto, pca__n_components=161; total time=   4.6s
[CV] END model__max_depth=1, model__max_features=auto, pca__n_components=161; total time=   4.4s
[CV] END model__max_depth=1, model__max_features=auto, pca__n_components=163; total time=   4.4s
[CV] END model__max_depth=1, model__max_features=auto, pca__n_components=163; total time=   4.4s
[CV] END model__max_depth=1, model__max_features=auto, pca__n_components=165; total time=   4.4s
[CV] END model__max_depth=1, model__max_features=auto, pca__n_components=165; total time=   4.5s
[CV] END model__max_depth=1, m

[CV] END model__max_depth=1, model__max_features=auto, pca__n_components=157; total time=   4.3s
[CV] END model__max_depth=1, model__max_features=auto, pca__n_components=157; total time=   4.4s
[CV] END model__max_depth=1, model__max_features=auto, pca__n_components=159; total time=   4.6s
[CV] END model__max_depth=1, model__max_features=auto, pca__n_components=159; total time=   4.5s
[CV] END model__max_depth=1, model__max_features=auto, pca__n_components=161; total time=17.4min
[CV] END model__max_depth=1, model__max_features=auto, pca__n_components=161; total time=   4.4s
[CV] END model__max_depth=1, model__max_features=auto, pca__n_components=161; total time=   4.2s
[CV] END model__max_depth=1, model__max_features=auto, pca__n_components=163; total time=   4.5s
[CV] END model__max_depth=1, model__max_features=auto, pca__n_components=163; total time=   4.4s
[CV] END model__max_depth=1, model__max_features=auto, pca__n_components=165; total time=   4.4s
[CV] END model__max_depth=1, m

[CV] END model__max_depth=1, model__max_features=auto, pca__n_components=159; total time=   4.5s
[CV] END model__max_depth=1, model__max_features=auto, pca__n_components=161; total time=17.4min
[CV] END model__max_depth=1, model__max_features=auto, pca__n_components=161; total time=   4.7s
[CV] END model__max_depth=1, model__max_features=auto, pca__n_components=161; total time=   4.4s
[CV] END model__max_depth=1, model__max_features=auto, pca__n_components=163; total time=   4.4s
[CV] END model__max_depth=1, model__max_features=auto, pca__n_components=163; total time=   4.4s
[CV] END model__max_depth=1, model__max_features=auto, pca__n_components=165; total time=   4.5s
[CV] END model__max_depth=1, model__max_features=auto, pca__n_components=165; total time=   4.4s
[CV] END model__max_depth=1, model__max_features=auto, pca__n_components=165; total time= 6.0min
[CV] END model__max_depth=1, model__max_features=auto, pca__n_components=167; total time=   4.6s
[CV] END model__max_depth=1, m


[CV] END model__max_depth=2, model__max_features=auto, pca__n_components=23; total time=   1.5s
[CV] END model__max_depth=2, model__max_features=auto, pca__n_components=25; total time=   1.8s
[CV] END model__max_depth=2, model__max_features=auto, pca__n_components=25; total time=   2.3s
[CV] END model__max_depth=2, model__max_features=auto, pca__n_components=27; total time=   1.5s
[CV] END model__max_depth=2, model__max_features=auto, pca__n_components=27; total time=   1.5s
[CV] END model__max_depth=2, model__max_features=auto, pca__n_components=27; total time=   1.6s
[CV] END model__max_depth=2, model__max_features=auto, pca__n_components=29; total time=   1.6s
[CV] END model__max_depth=2, model__max_features=auto, pca__n_components=29; total time=   1.8s
[CV] END model__max_depth=2, model__max_features=auto, pca__n_components=31; total time=   1.8s
[CV] END model__max_depth=2, model__max_features=auto, pca__n_components=31; total time=   1.8s
[CV] END model__max_depth=2, model__max

[CV] END model__max_depth=2, model__max_features=auto, pca__n_components=31; total time=   1.8s
[CV] END model__max_depth=2, model__max_features=auto, pca__n_components=31; total time=   2.0s
[CV] END model__max_depth=2, model__max_features=auto, pca__n_components=31; total time=   1.8s
[CV] END model__max_depth=2, model__max_features=auto, pca__n_components=33; total time=   1.9s
[CV] END model__max_depth=2, model__max_features=auto, pca__n_components=33; total time=   1.8s
[CV] END model__max_depth=2, model__max_features=auto, pca__n_components=35; total time=   1.9s
[CV] END model__max_depth=2, model__max_features=auto, pca__n_components=35; total time=   2.1s
[CV] END model__max_depth=2, model__max_features=auto, pca__n_components=35; total time=   2.1s
[CV] END model__max_depth=2, model__max_features=auto, pca__n_components=37; total time=   2.2s
[CV] END model__max_depth=2, model__max_features=auto, pca__n_components=37; total time=   2.4s
[CV] END model__max_depth=2, model__max_

In [ ]:
from IPython.display import display, Markdown

with open(Path.cwd().parent.parent.parent / "src" / "notebookcodesnippets" / "supervised" / "visualoptimalparameters.md", 'r') as fh:
    content = fh.read()

display(Markdown(content))
hide_toggle()

In [ ]:
visualize.principalComponentsVSscores(X = trainingData.drop(["material_id", "full_formula"], axis=1),
                                     ModelsBestParams = ModelsBestParams,
                                     prettyNames = prettyNames,
                                     numPC = numberOfPrincipalComponents,
                                     approach = InsertApproach)

In [ ]:
visualize.gridsearchVSscores(X = trainingData.drop(["material_id", "full_formula"], axis=1), 
                             ModelsBestParams = ModelsBestParams,
                            prettyNames = prettyNames,
                            approach = InsertApproach)

In [ ]:
from IPython.display import display, Markdown

with open(Path.cwd().parent.parent.parent / "src" / "notebookcodesnippets" / "supervised" / "roc-auc.md", 'r') as fh:
    content = fh.read()

display(Markdown(content))
hide_toggle() 

In [ ]:
SupervisedModels = pd.Series({}, dtype="string")

for i, algorithm in enumerate(Algorithms): 
    print("Current training algorithm: {}".format(prettyNames[i]))
    SupervisedModels[Abbreviations[i]] = (
        visualize.evaluatePrecisionRecallMetrics(classifier  = algorithm, 
                                     X = trainingData.drop(["material_id", "full_formula"], axis=1), 
                                     y = trainingTarget.values.reshape(-1,),
                                     k = numberSplits,
                                     n = numberRuns,
                                    cv = rskfold,
                     featureImportance = True,
                                 title = prettyNames[i],
                                 numPC = numberOfPrincipalComponents,
                              approach = InsertApproach )
    )

In [ ]:
from IPython.display import display, Markdown

with open(Path.cwd().parent.parent.parent / "src" / "notebookcodesnippets" / "supervised" / "visualize-cv.md", 'r') as fh:
    content = fh.read()

display(Markdown(content))
hide_toggle()

In [ ]:
visualize.plot_accuracy(SupervisedModels, prettyNames,                                       
                     prettyNames = prettyNames,
                           numPC = numberOfPrincipalComponents,
                        approach = InsertApproach)

In [ ]:
from IPython.display import display, Markdown

with open(Path.cwd().parent.parent.parent / "src" / "notebookcodesnippets" / "supervised" / "visualizerelevant.md", 'r') as fh:
    content = fh.read()

display(Markdown(content))
hide_toggle()

In [ ]:
visualize.plot_important_features(SupervisedModels,
                               X = trainingData.drop(["material_id", "full_formula"], axis=1),
                               k = numberSplits, 
                               n = numberRuns,                                      
                     prettyNames = prettyNames,
                           numPC = numberOfPrincipalComponents,
                        approach = InsertApproach)

In [ ]:
# #############################################################################
# Plot calibration plots
from sklearn.calibration import CalibratedClassifierCV,calibration_curve
import matplotlib.pyplot as plt
plt.figure(figsize=(10, 10))
ax1 = plt.subplot2grid((3, 1), (0, 0), rowspan=2)
ax2 = plt.subplot2grid((3, 1), (2, 0))

ax1.plot([0, 1], [0, 1], "k:", label="Perfectly calibrated")



# Randomly sample 70% of your dataframe
X_train = trainingData.sample(frac=0.3).drop(["material_id", "full_formula"], axis=1)
y_train = trainingTarget[X_train.index]
print(X_train.shape, y_train.shape)

X_test = trainingData.loc[~trainingData.index.isin(X_train.index)].drop(["material_id", "full_formula"], axis=1)
y_test = trainingTarget[X_test.index]

#print(X_test.shape,y_t)
#print(Algorithms[0])
lr = Algorithms[0]
dt = Algorithms[1]
rfc = Algorithms[2]
gb  = Algorithms[3]

rf_isotonic = CalibratedClassifierCV(rfc, cv=rskfold, method='isotonic')
print(lr)
for clf, name in [(lr, 'Logistic regression'),
                  (dt, 'Decision tree'),
                  (rfc, 'Random forest'),
                  (rf_isotonic, "Random forest calibrated"),
                  (gb, 'Gradient boost')]:
    
    clf.fit(X_train, y_train)
    
    if hasattr(clf, "predict_proba"):
        prob_pos = clf.predict_proba(X_test)[:, 1]
    else:  # use decision function
        prob_pos = clf.decision_function(X_test)
        prob_pos = \
            (prob_pos - prob_pos.min()) / (prob_pos.max() - prob_pos.min())
    fraction_of_positives, mean_predicted_value = \
        calibration_curve(y_test, prob_pos, n_bins=10)

    ax1.plot(mean_predicted_value, fraction_of_positives, "s-",
             label="%s" % (name, ))

    ax2.hist(prob_pos, range=(0, 1), bins=10, label=name,
             histtype="step", lw=2)

ax1.set_ylabel("Fraction of positives")
ax1.set_ylim([-0.05, 1.05])
ax1.legend(loc="lower right")
ax1.set_title('Calibration plots  (reliability curve)')

ax2.set_xlabel("Mean predicted value")
ax2.set_ylabel("Count")
ax2.legend(loc="upper center", ncol=2)

plt.tight_layout()
plt.show()

In [ ]:
from IPython.display import display, Markdown

with open(Path.cwd().parent.parent.parent / "src" / "notebookcodesnippets" / "supervised" / "falselypredicted.md", 'r') as fh:
    content = fh.read()

display(Markdown(content))
hide_toggle()

In [ ]:
visualize.plot_confusion_metrics(SupervisedModels, prettyNames, trainingData,
                                 k = numberSplits,
                                 n = numberRuns, 
                       prettyNames = prettyNames,
                             numPC = numberOfPrincipalComponents,
                          approach = InsertApproach)

In [ ]:
visualize.confusion_matrixQT(SupervisedModels, trainingTarget,                      
                             prettyNames = prettyNames,
                           numPC = numberOfPrincipalComponents,
                        approach = InsertApproach)

In [ ]:
from IPython.display import display, Markdown

with open(Path.cwd().parent.parent.parent / "src" / "notebookcodesnippets" / "supervised" / "predictions.md", 'r') as fh:
    content = fh.read()

display(Markdown(content))
hide_toggle()

In [ ]:
Summary                 = pd.DataFrame({}, dtype="string")
Summary["material_id"]  = testSet["material_id"]
Summary["full_formula"] = testSet["full_formula"]
Summary["pretty_formula"] = testSet["pretty_formula"]

PredictedCandidates = pd.Series({}, dtype="string")

threshold = numberSplits*numberRuns/2 #50% when equal
trainSet = trainingData.drop(["material_id", "full_formula"], axis=1)
testData = testSet.drop(["pretty_formula", "candidate", "full_formula", "material_id"], axis=1)
fittedAlgorithms = [] 

for i, algorithm in tqdm(enumerate(Algorithms)):
    
    # Train the final model with the best estimators
    fittedAlgorithm = train_model.fitAlgorithm(algorithm, 
                                    trainingData   = trainSet,#trainSet[trainSet.columns[SupervisedModels[Abbreviations[i]]["importantKeys"]>threshold]],\
                                    trainingTarget = trainingTarget.values.reshape(-1,),)
    
    fittedAlgorithms.append(fittedAlgorithm)
    
    # Predict the final model on unseen data
    PredictedCandidates[Abbreviations[i]],\
    PredictedCandidates[Abbreviations[i]+"Prob"] = predict_model.runPredictions(fittedAlgorithm,\
                                                        testData = testData)#[testData.columns[SupervisedModels[Abbreviations[i]]["importantKeys"]>threshold]])

In [ ]:
for abbreviation in Abbreviations:
    Summary[abbreviation]            = PredictedCandidates[abbreviation]
    Summary[abbreviation + "Prob"]   = PredictedCandidates[abbreviation + "Prob"]
    print("{} predict the number of candidates as: {}".format(abbreviation, int(np.sum(PredictedCandidates[abbreviation]))))

In [ ]:
Summary

In [ ]:
from IPython.display import display, Markdown

with open(Path.cwd().parent.parent.parent / "src" / "notebookcodesnippets" / "supervised" / "save.md", 'r') as fh:
    content = fh.read()

display(Markdown(content))
hide_toggle()

In [ ]:
file_path = Path(models_dir / InsertApproach / "trained-models")
Path(file_path).mkdir(parents=True, exist_ok=True)
for i, fitted_algorithm in tqdm(enumerate(fittedAlgorithms)):
    file_path = Path(models_dir / InsertApproach / "trained-models" / Path("PCA-" + str(numberOfPrincipalComponents) + "-" + prettyNames[i] + ".pkl"))
    with file_path.open("wb") as fp:
        pickle.dump(fitted_algorithm, fp)
        

file_path = (models_dir / InsertApproach /  "summary")
Path(Path(models_dir / InsertApproach /  "summary")).mkdir(parents=True, exist_ok=True)

file_path = Path(models_dir / InsertApproach /  "summary" / Path("PCA-" + str(numberOfPrincipalComponents) + "-" + "summary.pkl"))
with file_path.open("wb") as fp:
        pickle.dump(Summary, fp)